In [1]:
from datasets import load_dataset

In [2]:
import spacy

In [3]:
ds = load_dataset("argilla/medical-domain")
train_data = ds['train']

Using the latest cached version of the dataset since argilla/medical-domain couldn't be found on the Hugging Face Hub
Found the latest cached dataset configuration 'default' at /Users/Corina/.cache/huggingface/datasets/argilla___medical-domain/default/0.0.0/0f3e7aab79bf370979764275e3d12d74d8235bc6 (last modified on Tue Oct  1 17:43:31 2024).


In [ ]:
#!pip install spacy

In [7]:
def inspect_data(data, num_samples=5):
    # Print out the full structure of dataset
    for i, item in enumerate(data[:num_samples], 1):
        print(f"Features {i}: {item}\n")

    # Print out the structure and content of the first few data entries
    for i in range(num_samples):
        sample = data[i]
        print(f"Sample {i+1}: {sample}\n")

# Run the inspection of data
inspect_data(train_data)

Features 1: text

Features 2: inputs

Features 3: prediction

Features 4: prediction_agent

Features 5: annotation

Features 6: annotation_agent

Features 7: multi_label

Features 8: explanation

Features 9: id

Features 10: metadata

Features 11: status

Features 12: event_timestamp

Features 13: metrics

Sample 1: {'text': 'PREOPERATIVE DIAGNOSIS:,  Iron deficiency anemia.,POSTOPERATIVE DIAGNOSIS:,  Diverticulosis.,PROCEDURE:,  Colonoscopy.,MEDICATIONS: , MAC.,PROCEDURE: , The Olympus pediatric variable colonoscope was introduced into the rectum and advanced carefully through the colon to the cecum identified by the ileocecal valve and the appendiceal orifice.  Preparation was good, although there was some residual material in the cecum that was difficult to clear completely.  The mucosa was normal throughout the colon.  No polyps or other lesions were identified, and no blood was noted.  Some diverticula were seen of the sigmoid colon with no luminal narrowing or evidence of inflamm

## Standard and potential new NER types
standard NER types: Persons, dates, locations, organizations (ex. department)


new NER types: treatment, disease, symptom, drug

## Apply the standard NER classifier of spaCy to your data

In [8]:
#!python -m spacy download en_core_web_sm


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 2.6 MB/s eta 0:00:0000:0100:01
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')


In [9]:
import spacy

nlp = spacy.load("en_core_web_sm")

for i, text in enumerate(train_data['text']):
    doc = nlp(text)
    print(f"Sample {i+1} Entities:")
    for ent in doc.ents:
        print(f"Entity: {ent.text}, Label: {ent.label_}")
    print("-" * 50)

Sample 1 Entities:
Entity: Olympus, Label: ORG
Entity: retroflex, Label: NORP
Entity: X, Label: PERSON
Entity: 2 years, Label: DATE
--------------------------------------------------
Sample 2 Entities:
Entity: Normal, Label: PERSON
Entity: Selective, Label: PERSON
Entity: LV gram., Label: PERSON
Entity: Mynx, Label: PERSON
Entity: DETAIL, Label: ORG
Entity: anesthesia, Label: GPE
Entity: 2%, Label: PERCENT
Entity: 6, Label: CARDINAL
Entity: 6-French, Label: NORP
Entity: 6-French, Label: NORP
Entity: LV gram, Label: PERSON
Entity: 6, Label: CARDINAL
Entity: Post LV gram, Label: WORK_OF_ART
Entity: Mynx, Label: PERSON
Entity: LVEDP, Label: PERSON
Entity: 9, Label: DATE
Entity: LAD, Label: GPE
Entity: 50% to 60%, Label: PERCENT
Entity: 40%, Label: PERCENT
Entity: LAD, Label: ORG
Entity: 50% to 60%, Label: PERCENT
Entity: RCA, Label: ORG
Entity: 40%, Label: PERCENT
Entity: 60%.,PLAN, Label: CARDINAL
Entity: LAD, Label: ORG
--------------------------------------------------
Sample 3 Entitie

In [10]:
from sklearn.metrics import classification_report
from sklearn.preprocessing import MultiLabelBinarizer
import random

# Prepare your data
texts = train_data['text']
labels = train_data['annotation']

# Randomly sample 100 texts for evaluation
sample_texts = random.sample(texts, 100)
sample_labels = random.sample(labels, 100)

# Predict and evaluate
y_true = []
y_pred = []

for text, true_entities in zip(sample_texts, sample_labels):
    doc = nlp(text)
    predicted_entities = [(ent.text, ent.label_) for ent in doc.ents]

    # Store results
    y_true.append(set(true_entities))
    y_pred.append(set(predicted_entities))

# Binarize for sklearn's classification report
mlb = MultiLabelBinarizer()
y_true_bin = mlb.fit_transform(y_true)
y_pred_bin = mlb.transform(y_pred)

# Classification report
print(classification_report(y_true_bin, y_pred_bin, target_names=mlb.classes_))


TypeError: 'NoneType' object is not iterable